In [1]:
from pyccx import *
import numpy as np
from interface import DynamicUnderRelaxation, InterfaceData, RelativeCovergenceMonitor, AbsCovergenceMonitor, ConstantUnderRelaxation
from mapper import generate_mapper
from add_pyofm import pyofm_path
import sys
sys.path.append(pyofm_path)
import pyofm as ofm
import time

In [2]:
ccx_logoff = True
if ccx_logoff:
    import logging
    logger = logging.getLogger('PYCCX')
    logger.setLevel(logging.CRITICAL)

use_relax = True
under_relax_obj = DynamicUnderRelaxation
init_omega = 0.95

# tolerance setting
tol = 1e-3
if tol > 1e-1:
    print('The tolerance is too large, this may lead to instability or low quality results')

In [3]:
tpoint = time.time()
solverF = ofm.make_solver('buoyantPimpleFoam' ,kase='fluid')
solverF.create_fields()
solverF.initialize()
solverF.enable_backup_restore()
dt = solverF.init_dt()
iface = ofm.iface.InterfaceAdapter(solverF, 'interface')
fnodes = iface.extract_centres()
ftempAdap = ofm.CHT.TemperatureAdapter(iface)
ffluxAdap = ofm.CHT.HeatFluxAdapter(iface)
fluid_prepare_time = time.time()-tpoint
print(fluid_prepare_time)

0.1627180576324463


In [4]:
# solid solver
tpoint = time.time()
jobname = 'solid/solidNbi0.1'
output = 'asc'
prob = Problem(jobname=jobname, output=output)
msolver = prob.get_solver()
msolver.initailize()
# since we know there is one step
# we stop b4 it
msolver.solve(stopb4step=1)
nlgeom = msolver.get_nlgeomsolver()
nlgeom.initialize()

# initialize our interface set
iset = nlgeom.get_set(
    set_name='Interface',
    set_type='sfelem',
    is_surface=True
)
nset = nlgeom.get_set(
    set_name='Inodes',
    set_type='node',
    is_surface=True
)

# retrieve geometry data
snodes = nset.coordinates()
scents = iset.extract_face_centers()

# create cht adapter
solverS = CHTAdapter(nlgeom=nlgeom)
solverS.add_interface(set_acc=nset, is_settable=False, itype=CHTAdapter.TEMP)
solverS.add_interface(set_acc=iset, is_settable=True, itype=CHTAdapter.DFLUX)

# now we are ready
solid_prepare_time = time.time()-tpoint
print(solid_prepare_time)

0.020139455795288086


In [5]:
tpoint = time.time()
Tf = 'Tf'
Ts = 'Ts'
Ff = 'Ff'
Fs = 'Fs'
Ff2Fs = {Ff:Fs}
Ts2Tf = {Ts:Tf}
f2s_mapper, s2f_mapper = generate_mapper(fnodes, [scents, snodes], Ff2Fs, Ts2Tf,r1=0.013,r2=0.02)
mapper_construct_time = time.time()-tpoint
print(mapper_construct_time)

0.22174620628356934


In [6]:
# coupling data and setups
fluxF = InterfaceData(size=fnodes.shape[0], value=0.0)
fluxS = InterfaceData(size=scents.shape[0], value=0.0)
tempF = InterfaceData(size=fnodes.shape[0], value=1000.0)
tempS = InterfaceData(size=snodes.shape[0], value=600.0) # initial guess
thetaT = InterfaceData(size=fnodes.shape[0], value=0.0)

under_relax = under_relax_obj(init_omega=init_omega)
conv_mntr = RelativeCovergenceMonitor(tol=tol)
conv_solution = AbsCovergenceMonitor(tol=1e-4)

# maximum pc steps allowed
max_pc_steps = 200

In [7]:
# coupling timing information, use fixed time step for now
# Tfinal = 1.0
# N = 100
# dt = Tfinal/N
tF = 10.0
DT = 10.0*dt
avg_pc_iterations = 0.0
flog = open('FDSN_DYSOLID.log', mode='w')
flog.write('Fluid Dirichlet with solid Neumann setting\n')
flog.close()
flog = open('FDSN_DYSOLID.log', mode='a')
flog.write(
    '\nFluid initialization time: %f\nSolid initialization time: %f\nMapper constuction time: %f\n\n' % \
    (fluid_prepare_time, solid_prepare_time, mapper_construct_time)
)

108

In [8]:
t = 0.0
step = 0

In [9]:
def tol(idata):
    return np.linalg.norm(idata.res)/np.linalg.norm(idata.curr)

In [10]:
tpoint = time.time()
# begin to couple
while t <= tF+1e-6:
    t += DT
    
    pc_counts = 0
    
    # back up solutions
    solverF.backup_state()
    solverS.backup_state()
    
    # mapping, T:s->f
    s2f_mapper.put(Ts, tempS.curr)
    s2f_mapper.apply(Ts, Tf)
    tempF.curr[:] = s2f_mapper.get(Tf)
    
    # update fluid interface temperature
    ftempAdap.assign(tempF.curr)
    
    while True:
        # back up previous interface value
        tempF.backup()
        
        # advance fluid
        solverF.subcycle(DT)
        # retrieve fluid interface flux
        fluxF.curr[:] = ffluxAdap.extract()
        
        # mapping, F:f->s
        f2s_mapper.put(Ff, fluxF.curr)
        f2s_mapper.apply(Ff, Fs)
        fluxS.curr[:] = f2s_mapper.get(Fs)
        # update the distributed heat fluxes on solid interface
        solverS['Interface', SET].set_dfluxes(fluxS.curr)
        
        # advance solid
        solverS.adjust_timesize(DT)
        solverS.increment()
        tempS.curr[:] = solverS['Inodes', GET].get_temperatures()
        
        # mapping, T:s->f
        s2f_mapper.put(Ts, tempS.curr)
        s2f_mapper.apply(Ts, Tf)
        tempF.curr[:] = s2f_mapper.get(Tf)
        
        # update residual
        tempF.update_res()
        
        # test convergence
        is_conv = conv_mntr.determine_convergence(tempF)
        if is_conv or pc_counts >= max_pc_steps:
            # notice the solid side to advance
            solverS.finish_increment()
            solverF.advance()
            dt = solverF.dt()
            DT = 10.0*dt
            if t + DT > tF:
                DT = tf-t
            break
        else:
            # if not converge, then underrelaxation and update to fluid then restore
            if use_relax:
                under_relax.determine_omega(tempF, step, pc_counts)
                under_relax.update_solution(tempF)
            # update the underelaxed interface temperature
            # make sure that restoring the fluid solver will
            # not affect the newly updated values
            solverF.restore_state()
            ftempAdap.assign(tempF.curr)
            solverS.restore_state()
            solverS.finish_increment()
            pc_counts = pc_counts + 1
            if pc_counts > 20 and pc_counts % 5 == 0:
                print('WARNING too slow convergence for step %d with correction iterations %d, current relative error %e..' % (step+1, pc_counts, tol(tempF)))

    # outputs
    step += 1
    msg = 'step=%d: res=%e, coupling_dt=%f, time=%f, pc_iterations=%i.' % (step, tol(tempF), DT, t, pc_counts)
    print(msg)
    flog.write(msg+'\n')
    avg_pc_iterations += pc_counts

nlgeom.finalize()
msolver.solve(skipsolve=True)
msolver.finalize()

solving_time=  time.time()-tpoint
flog.write('\nSolving time: %f\n' % solving_time)
flog.close()

step=1: res=4.094441e-04, coupling_dt=0.000206, time=0.000000, pc_iterations=1.
step=2: res=6.665684e-04, coupling_dt=0.000136, time=0.000207, pc_iterations=6.
step=3: res=5.373017e-04, coupling_dt=0.000152, time=0.000342, pc_iterations=3.
step=4: res=3.042282e-04, coupling_dt=0.000040, time=0.000494, pc_iterations=4.
step=5: res=8.818099e-04, coupling_dt=0.000048, time=0.000534, pc_iterations=2.
step=6: res=7.266617e-04, coupling_dt=0.000107, time=0.000582, pc_iterations=5.
step=7: res=2.582553e-04, coupling_dt=0.000136, time=0.000689, pc_iterations=3.
step=8: res=1.744530e-04, coupling_dt=0.000175, time=0.000825, pc_iterations=7.
step=9: res=6.594626e-04, coupling_dt=0.000187, time=0.001001, pc_iterations=3.
step=10: res=1.592432e-04, coupling_dt=0.000184, time=0.001187, pc_iterations=2.
step=11: res=2.633802e-04, coupling_dt=0.000157, time=0.001371, pc_iterations=2.
step=12: res=7.097923e-04, coupling_dt=0.000129, time=0.001528, pc_iterations=2.
step=13: res=3.363566e-04, coupling_d

step=103: res=8.948888e-04, coupling_dt=0.000101, time=0.008934, pc_iterations=0.
step=104: res=4.051335e-04, coupling_dt=0.000045, time=0.009035, pc_iterations=0.
step=105: res=6.829786e-04, coupling_dt=0.000048, time=0.009080, pc_iterations=0.
step=106: res=3.863631e-04, coupling_dt=0.000052, time=0.009128, pc_iterations=0.
step=107: res=6.859050e-04, coupling_dt=0.000059, time=0.009180, pc_iterations=0.
step=108: res=3.563973e-04, coupling_dt=0.000073, time=0.009240, pc_iterations=0.
step=109: res=8.160023e-04, coupling_dt=0.000108, time=0.009312, pc_iterations=0.
step=110: res=2.315944e-04, coupling_dt=0.000090, time=0.009421, pc_iterations=0.
step=111: res=7.656769e-04, coupling_dt=0.000172, time=0.009510, pc_iterations=0.
step=112: res=3.071244e-04, coupling_dt=0.000032, time=0.009682, pc_iterations=0.
step=113: res=2.042227e-04, coupling_dt=0.000035, time=0.009714, pc_iterations=0.
step=114: res=2.857776e-04, coupling_dt=0.000037, time=0.009749, pc_iterations=0.
step=115: res=1.

step=203: res=2.809442e-04, coupling_dt=0.000138, time=0.015071, pc_iterations=0.
step=204: res=5.267801e-04, coupling_dt=0.000115, time=0.015209, pc_iterations=0.
step=205: res=6.712314e-04, coupling_dt=0.000129, time=0.015324, pc_iterations=0.
step=206: res=8.572977e-04, coupling_dt=0.000160, time=0.015453, pc_iterations=1.
step=207: res=3.564594e-04, coupling_dt=0.000109, time=0.015613, pc_iterations=0.
step=208: res=5.494684e-04, coupling_dt=0.000092, time=0.015722, pc_iterations=0.
step=209: res=3.816865e-04, coupling_dt=0.000181, time=0.015814, pc_iterations=0.
step=210: res=7.835239e-04, coupling_dt=0.000113, time=0.015995, pc_iterations=0.
step=211: res=6.059389e-04, coupling_dt=0.000115, time=0.016108, pc_iterations=0.
step=212: res=8.328435e-04, coupling_dt=0.000125, time=0.016222, pc_iterations=0.
step=213: res=8.858935e-04, coupling_dt=0.000188, time=0.016347, pc_iterations=0.
step=214: res=9.541430e-04, coupling_dt=0.000188, time=0.016535, pc_iterations=0.
step=215: res=6.

step=303: res=3.179784e-05, coupling_dt=0.000030, time=0.024277, pc_iterations=0.
step=304: res=1.428347e-05, coupling_dt=0.000032, time=0.024307, pc_iterations=0.
step=305: res=2.786276e-05, coupling_dt=0.000035, time=0.024339, pc_iterations=0.
step=306: res=1.841815e-05, coupling_dt=0.000037, time=0.024374, pc_iterations=0.
step=307: res=4.511470e-04, coupling_dt=0.000040, time=0.024411, pc_iterations=0.
step=308: res=7.021806e-04, coupling_dt=0.000042, time=0.024451, pc_iterations=0.
step=309: res=4.336262e-04, coupling_dt=0.000045, time=0.024493, pc_iterations=0.
step=310: res=2.392977e-04, coupling_dt=0.000049, time=0.024538, pc_iterations=0.
step=311: res=4.917302e-04, coupling_dt=0.000053, time=0.024587, pc_iterations=0.
step=312: res=2.531105e-04, coupling_dt=0.000061, time=0.024640, pc_iterations=0.
step=313: res=2.400374e-04, coupling_dt=0.000076, time=0.024701, pc_iterations=0.
step=314: res=1.520486e-04, coupling_dt=0.000118, time=0.024777, pc_iterations=0.
step=315: res=3.

step=404: res=1.346140e-04, coupling_dt=0.000177, time=0.028157, pc_iterations=0.
step=405: res=1.927591e-05, coupling_dt=0.000087, time=0.028335, pc_iterations=0.
step=406: res=5.271594e-05, coupling_dt=0.000159, time=0.028421, pc_iterations=0.
step=407: res=8.601406e-05, coupling_dt=0.000099, time=0.028580, pc_iterations=0.
step=408: res=1.710501e-05, coupling_dt=0.000031, time=0.028679, pc_iterations=0.
step=409: res=3.599095e-05, coupling_dt=0.000033, time=0.028709, pc_iterations=0.
step=410: res=7.588942e-06, coupling_dt=0.000035, time=0.028742, pc_iterations=0.
step=411: res=2.964202e-05, coupling_dt=0.000038, time=0.028777, pc_iterations=0.
step=412: res=4.418448e-06, coupling_dt=0.000040, time=0.028815, pc_iterations=0.
step=413: res=2.787304e-05, coupling_dt=0.000043, time=0.028855, pc_iterations=0.
step=414: res=4.451197e-04, coupling_dt=0.000046, time=0.028898, pc_iterations=0.
step=415: res=6.939599e-04, coupling_dt=0.000049, time=0.028944, pc_iterations=0.
step=416: res=4.

...

step=82392: res=7.114296e-04, coupling_dt=0.000188, time=5.834573, pc_iterations=0.
step=82393: res=6.352727e-04, coupling_dt=0.000188, time=5.834761, pc_iterations=0.
step=82394: res=6.214109e-04, coupling_dt=0.000187, time=5.834948, pc_iterations=0.
step=82395: res=6.253895e-04, coupling_dt=0.000177, time=5.835135, pc_iterations=0.
step=82396: res=6.506700e-04, coupling_dt=0.000085, time=5.835313, pc_iterations=0.
step=82397: res=7.570533e-04, coupling_dt=0.000153, time=5.835398, pc_iterations=0.
step=82398: res=8.100087e-04, coupling_dt=0.000041, time=5.835550, pc_iterations=0.
step=82399: res=9.421332e-04, coupling_dt=0.000044, time=5.835591, pc_iterations=0.
step=82400: res=9.545589e-04, coupling_dt=0.000047, time=5.835635, pc_iterations=0.
step=82401: res=9.394164e-04, coupling_dt=0.000051, time=5.835682, pc_iterations=0.
step=82402: res=9.591388e-04, coupling_dt=0.000057, time=5.835733, pc_iterations=0.
step=82403: res=9.558033e-04, coupling_dt=0.000067, time=5.835789, pc_iterat

step=82492: res=4.052445e-05, coupling_dt=0.000031, time=5.843747, pc_iterations=0.
step=82493: res=3.297611e-05, coupling_dt=0.000033, time=5.843778, pc_iterations=0.
step=82494: res=2.836446e-05, coupling_dt=0.000035, time=5.843811, pc_iterations=0.
step=82495: res=2.573085e-05, coupling_dt=0.000038, time=5.843846, pc_iterations=0.
step=82496: res=2.453925e-05, coupling_dt=0.000040, time=5.843883, pc_iterations=0.
step=82497: res=3.477216e-04, coupling_dt=0.000043, time=5.843924, pc_iterations=0.
step=82498: res=6.025337e-04, coupling_dt=0.000046, time=5.843967, pc_iterations=0.
step=82499: res=4.948856e-04, coupling_dt=0.000050, time=5.844013, pc_iterations=0.
step=82500: res=4.739451e-04, coupling_dt=0.000055, time=5.844062, pc_iterations=0.
step=82501: res=5.192224e-04, coupling_dt=0.000063, time=5.844117, pc_iterations=0.
step=82502: res=6.220088e-04, coupling_dt=0.000081, time=5.844180, pc_iterations=0.
step=82503: res=6.532738e-04, coupling_dt=0.000135, time=5.844260, pc_iterat

step=82592: res=3.401157e-04, coupling_dt=0.000096, time=5.848473, pc_iterations=0.
step=82593: res=5.156889e-04, coupling_dt=0.000012, time=5.848569, pc_iterations=0.
step=82594: res=3.780889e-04, coupling_dt=0.000013, time=5.848581, pc_iterations=0.
step=82595: res=1.201726e-04, coupling_dt=0.000014, time=5.848594, pc_iterations=0.
step=82596: res=2.418197e-04, coupling_dt=0.000015, time=5.848608, pc_iterations=0.
step=82597: res=3.189445e-04, coupling_dt=0.000016, time=5.848623, pc_iterations=0.
step=82598: res=9.724779e-05, coupling_dt=0.000017, time=5.848639, pc_iterations=0.
step=82599: res=4.822031e-05, coupling_dt=0.000018, time=5.848656, pc_iterations=0.
step=82600: res=2.193377e-05, coupling_dt=0.000020, time=5.848674, pc_iterations=0.
step=82601: res=1.272716e-05, coupling_dt=0.000021, time=5.848694, pc_iterations=0.
step=82602: res=7.168042e-06, coupling_dt=0.000022, time=5.848715, pc_iterations=0.
step=82603: res=4.607806e-06, coupling_dt=0.000024, time=5.848737, pc_iterat

step=82691: res=6.026487e-07, coupling_dt=0.000035, time=5.852527, pc_iterations=0.
step=82692: res=5.434487e-07, coupling_dt=0.000037, time=5.852562, pc_iterations=0.
step=82693: res=5.144840e-07, coupling_dt=0.000040, time=5.852599, pc_iterations=0.
step=82694: res=5.104995e-07, coupling_dt=0.000043, time=5.852639, pc_iterations=0.
step=82695: res=5.300859e-07, coupling_dt=0.000046, time=5.852682, pc_iterations=0.
step=82696: res=5.751099e-07, coupling_dt=0.000049, time=5.852727, pc_iterations=0.
step=82697: res=6.516028e-07, coupling_dt=0.000054, time=5.852776, pc_iterations=0.
step=82698: res=7.762900e-07, coupling_dt=0.000061, time=5.852830, pc_iterations=0.
step=82699: res=9.845268e-07, coupling_dt=0.000077, time=5.852892, pc_iterations=0.
step=82700: res=1.366297e-06, coupling_dt=0.000122, time=5.852969, pc_iterations=0.
step=82701: res=2.184639e-06, coupling_dt=0.000182, time=5.853092, pc_iterations=0.
step=82702: res=3.959608e-06, coupling_dt=0.000128, time=5.853273, pc_iterat

KeyboardInterrupt: 